In [1]:
import os
import shutil
import warnings
import urllib.request as request
from contextlib import closing

import cupy

import dask_cudf
import dask_ml

from cuml.manifold import UMAP as cuUMAP
from cuml.dask.decomposition import PCA as cuDaskPCA
from cuml.dask.cluster import KMeans as cuDaskKMeans
from cuml.dask.manifold import UMAP as cuDaskUMAP

from dask.distributed import Client, LocalCluster
from dask_cuda import initialize, LocalCUDACluster
from dask_cuda.local_cuda_cluster import cuda_visible_devices

from bokeh.io.export import export_png
from bokeh.plotting import figure
from bokeh.models.tickers import FixedTicker
from bokeh.io import output_notebook, push_notebook, show

from nvidia.cheminformatics.chembldata import ChEmblData

warnings.filterwarnings('ignore', 'Expected ')
warnings.simplefilter('ignore')

output_notebook()

Loading BokehJS ...

### Configurations and settings

In [2]:
# Please add or remove device ids that can be used
# CUDA_VISIBLE_DEVICES=[0]
CUDA_VISIBLE_DEVICES = cuda_visible_devices(0).split(',')

pca_comps = 64
n_clusters = 6
n_neighbors=100
num_cols=500000

enable_tcp_over_ucx = True
enable_nvlink = False
enable_infiniband = False

COLORS = ["#406278", "#e32636", "#9966cc", "#cd9575", "#915c83", "#008000",
          "#ff9966", "#848482", "#8a2be2", "#de5d83", "#800020", "#e97451",
          "#5f9ea0", "#36454f", "#008b8b", "#e9692c", "#f0b98d", "#ef9708",
          "#0fcfc0", "#9cded6", "#d5eae7", "#f3e1eb", "#f6c4e1", "#f79cd4"]

### Functions

In [3]:
def show_cluster_plot(ldcudf, title='UMAP'):
    """
    Draws a scatter plots from output of UMAP.
    """
    umap_fig = figure(title=title, width=800, output_backend="webgl")
    clusters = ldcudf['cluster'].unique().compute().values_host

    for cluster in clusters:
        query = 'cluster == %s' % (cluster)

        cdf = ldcudf.query(query)
        cdf = cdf.compute()

        if cdf.shape[0] == 0:
            continue

        x_array = cupy.fromDlpack(cdf['x'].to_dlpack())
        y_array = cupy.fromDlpack(cdf['y'].to_dlpack())

        umap_fig.circle(x_array.get(),
                        y_array.get(),
                        size=2,
                        color=COLORS[cluster],
                        alpha=0.5, legend = 'Cluster ' + str(cluster))

    umap_fig.legend.location = 'top_right'
    umap_fig.legend.title = 'Clusters'
    
    umap_fig_handle = show(umap_fig, notebook_handle=True)
    push_notebook(handle=umap_fig_handle)
    

def recluster(tcdf):
    """
    Recluster on a dataset
    """
    tcdf = tcdf.persist()

    print('Reclustering...')
    tcdf = tcdf.drop(['x', 'y', 'cluster'], axis=1)

    print('Computing KMEANS...')
    kmeans_float = cuDaskKMeans(client=client, n_clusters=n_clusters)
    kmeans_float.fit(tcdf)
    kmeans_labels = kmeans_float.predict(tcdf)

    print('Computing UMAP...')
    local_model = cuUMAP()
    X_train = tcdf.compute()
    local_model.fit(X_train)

    umap_model = cuDaskUMAP(local_model,
                            n_neighbors=n_neighbors,
                            a=1.0,
                            b=1.0,
                            learning_rate=1.0,
                            client=client)
    Xt = umap_model.transform(tcdf)

    # Add back the column required for plotting and to correlating data
    # between re-clustering
    tcdf['x'] = Xt[0]
    tcdf['y'] = Xt[1]
    tcdf['cluster'] = kmeans_labels
    
    return tcdf

# Download ChEMBL database

In [4]:
data_dir = "/data/db"
db_file = os.path.join(data_dir, 'chembl_27.db')

if not os.path.exists(db_file):
    print('Downloading ChEMBL db...')

    os.makedirs(data_dir, exist_ok=True)
    with closing(request.urlopen('ftp://ftp.ebi.ac.uk/pub/databases/chembl/ChEMBLdb/latest/chembl_27_sqlite.tar.gz')) as r:
        with open(db_file, 'wb') as f:
            shutil.copyfileobj(r, f)

    print('Download completed')
else:
    print('Reusing available ChEMBL db at', db_file)

Reusing available ChEMBL db at /data/db/chembl_27.db


In [5]:
cluster = LocalCUDACluster(protocol="ucx",
                           dashboard_address=':9001',
                           # TODO: automate visible device list
                           CUDA_VISIBLE_DEVICES=CUDA_VISIBLE_DEVICES,
                           enable_tcp_over_ucx=enable_tcp_over_ucx,
                           enable_nvlink=enable_nvlink,
                           enable_infiniband=enable_infiniband)
client = Client(cluster)
client

<Client: 'ucx://127.0.0.1:52925' processes=8 threads=8, memory=540.95 GB>

# Generate fingerprint from ChEMBL

The 4 in ECFP4 corresponds to the diameter of the atom environments considered, while the Morgan fingerprints take a radius parameter. So a Morgan fingerprint with radius=2 is roughly equivalent to ECFP4 and FCFP4.

In [6]:
%%time
chem_data = ChEmblData(db_file=db_file)

# Fetch and generate Finger prints
ddf = chem_data.fetch_all_props(num_recs=num_cols)

dcudf = dask_cudf.from_dask_dataframe(ddf)
dcudf = dcudf.persist()

# Reduce
pca = cuDaskPCA(client=client, n_components=pca_comps)
dcudf = pca.fit_transform(dcudf)

CPU times: user 4.78 s, sys: 1.73 s, total: 6.5 s
Wall time: 58 s


# Clustering

In [7]:
%%time

kmeans_float = cuDaskKMeans(client=client, n_clusters=n_clusters)
kmeans_float.fit(dcudf)
kmeans_labels = kmeans_float.predict(dcudf)

CPU times: user 316 ms, sys: 44 ms, total: 360 ms
Wall time: 2.39 s


In [8]:
%%time
local_model = cuUMAP()
X_train = dcudf.compute()
local_model.fit(X_train)

umap_model = cuDaskUMAP(local_model,
                        n_neighbors=n_neighbors,
                        a=1.0,
                        b=1.0,
                        learning_rate=1.0,
                        client=client)
Xt = umap_model.transform(dcudf)

dcudf['x'] = Xt[0]
dcudf['y'] = Xt[1]
dcudf['cluster'] = kmeans_labels

dcudf.head(5)

CPU times: user 4 s, sys: 3.69 s, total: 7.69 s
Wall time: 8.87 s


0         1         2         3         4         5         6  \
0 -0.841262 -0.532689  0.593469 -0.300854 -0.386285  0.083089  0.298149   
1 -1.194547  0.077214  0.088086  0.026653 -0.621467 -0.009770  0.857470   
2 -0.826907 -0.318188 -0.032448 -0.191862 -0.852841 -1.226258 -0.008388   
3 -1.188910 -0.013077 -0.099945 -0.391775 -0.353217  0.021295  0.666827   
4 -1.083598 -0.216209  0.220645 -0.075503 -1.361563 -0.428661  0.113608   

          7         8         9  ...        57        58        59        60  \
0  1.064663  1.051399  0.059279  ... -0.302770  0.431579 -0.352560 -0.568256   
1  0.222389  0.639240 -0.193912  ... -0.107070  0.152501 -0.079606 -0.695219   
2  1.237544  0.505759 -0.199835  ...  0.266255  0.442445 -0.179173 -0.693805   
3 -0.002881  0.674717 -0.118623  ... -0.337403 -0.114876 -0.187541 -0.392496   
4  1.287328  1.162967  0.145863  ...  0.108748  0.510968 -0.149103 -0.995041   

         61        62        63         x         y  cluster  
0  0.647301 -0.012482  0.166395 -0.047803  0.530272        5  
1  0.571233  0.091814 -0.086819 -0.467398  0.090439        5  
2  0.717689  0.033196 -0.232645  0.134964  0.523269        5  
3  0.870016 -0.344060  0.211134 -0.731082  0.388636        5  
4  0.629160 -0.199390  0.115195 -0.122600  0.473448        5  

[5 rows x 67 columns]

In [9]:
%%time
show_cluster_plot(dcudf)

CPU times: user 8.48 s, sys: 2.34 s, total: 10.8 s
Wall time: 24.4 s


# Re-clustering

In [10]:
%%time
# Filter data before reclustering
cluster = 1                                         # <- PLEASE CHANGE CLUSTER AS REQUIRED
query = 'cluster == ' + str(cluster)
tcdf = dcudf.query(query)

show_cluster_plot(tcdf, title='UMAP - cluster ' + str(cluster))
tcdf = recluster(tcdf)
print('Plotting UMAP...')
show_cluster_plot(tcdf, title='UMAP - cluster ' + str(cluster))

Reclustering...
Computing KMEANS...
Computing UMAP...
Plotting UMAP...


CPU times: user 8.4 s, sys: 1.58 s, total: 9.98 s
Wall time: 23.9 s
